In [0]:
%pip install kaggle

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.7/12.7 MB 128.0 MB/s eta 0:00:00
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
import os

os.environ['KAGGLE_USERNAME'] = "<Username>"
os.environ['KAGGLE_KEY'] = "<KEY>"

print("Kaggle Credentials Configured")

Kaggle Credentials Configured


In [0]:
spark.sql("""
CREATE SCHEMA IF NOT EXISTS workspace.eccomerce
""")

DataFrame[]

In [0]:
spark.sql("""
CREATE VOLUME IF NOT EXISTS workspace.eccomerce.ecommerce_data
""")

DataFrame[]

In [0]:
%sh
cd /Volumes/workspace/eccomerce/ecommerce_data
kaggle datasets download -d mkechinov/ecommerce-behavior-data-from-multi-category-store
unzip -o ecommerce-behavior-data-from-multi-category-store.zip

Dataset URL: https://www.kaggle.com/datasets/mkechinov/ecommerce-behavior-data-from-multi-category-store
License(s): copyright-authors
ecommerce-behavior-data-from-multi-category-store.zip: Skipping, found more recently modified local copy (use --force to force download)
Archive:  ecommerce-behavior-data-from-multi-category-store.zip
  inflating: 2019-Nov.csv            
  inflating: 2019-Oct.csv            


In [0]:
oct_events = spark.read.csv(
    "/Volumes/workspace/eccomerce/ecommerce_data/2019-Oct.csv",
    header=True,
    inferSchema=True
)

nov_events = spark.read.csv(
    "/Volumes/workspace/eccomerce/ecommerce_data/2019-Nov.csv",
    header=True,
    inferSchema=True
)

In [0]:
events = spark.read.csv("/Volumes/workspace/ecommerce/ecommerce_data/2019-Oct.csv", header=True, inferSchema=True)

In [0]:
oct_events = spark.read.csv("/Volumes/workspace/eccomerce/ecommerce_data/2019-Oct.csv", header=True, inferSchema=True)

nov_events = spark.read.csv("/Volumes/workspace/eccomerce/ecommerce_data/2019-Nov.csv", header=True, inferSchema=True)

### 1.Read Data into Oct DataFrame

In [0]:
display(oct_events.limit(5))

event_time event_type product_id category_id category_code brand price user_id user_session 2019-10-01T00:00:00.000Z view 44600062 2103807459595387724 null shiseido 35.79 541312140 72d76fde-8bb3-4e00-8c23-a032dfed738c 2019-10-01T00:00:00.000Z view 3900821 2053013552326770905 appliances.environment.water_heater aqua 33.2 554748717 9333dfbd-b87a-4708-9857-6336556b0fcc 2019-10-01T00:00:01.000Z view 17200506 2053013559792632471 furniture.living_room.sofa null 543.1 519107250 566511c2-e2e3-422b-b695-cf8e6e792ca8 2019-10-01T00:00:01.000Z view 1307067 2053013558920217191 computers.notebook lenovo 251.74 550050854 7c90fc70-0e80-4590-96f3-13c02c18c713 2019-10-01T00:00:04.000Z view 1004237 2053013555631882655 electronics.smartphone apple 1081.98 535871217 c6bd7419-2748-4c56-95b4-8cec9ff8b80d

### 2.Read Data into NOV DataFrame

In [0]:
display(nov_events.limit(5))

event_time event_type product_id category_id category_code brand price user_id user_session 2019-11-01T00:00:00.000Z view 1003461 2053013555631882655 electronics.smartphone xiaomi 489.07 520088904 4d3b30da-a5e4-49df-b1a8-ba5943f1dd33 2019-11-01T00:00:00.000Z view 5000088 2053013566100866035 appliances.sewing_machine janome 293.65 530496790 8e5f4f83-366c-4f70-860e-ca7417414283 2019-11-01T00:00:01.000Z view 17302664 2053013553853497655 null creed 28.31 561587266 755422e7-9040-477b-9bd2-6a6e8fd97387 2019-11-01T00:00:01.000Z view 3601530 2053013563810775923 appliances.kitchen.washer lg 712.87 518085591 3bfb58cd-7892-48cc-8020-2f17e6de6e7f 2019-11-01T00:00:01.000Z view 1004775 2053013555631882655 electronics.smartphone xiaomi 183.27 558856683 313628f1-68b8-460d-84f6-cec7a8796ef2

### 3.Basic Operations

Select

In [0]:
oct_events.select("event_time", "event_type", "product_id", "price").show(5)

+-------------------+----------+----------+-------+
|         event_time|event_type|product_id|  price|
+-------------------+----------+----------+-------+
|2019-10-01 00:00:00|      view|  44600062|  35.79|
|2019-10-01 00:00:00|      view|   3900821|   33.2|
|2019-10-01 00:00:01|      view|  17200506|  543.1|
|2019-10-01 00:00:01|      view|   1307067| 251.74|
|2019-10-01 00:00:04|      view|   1004237|1081.98|
+-------------------+----------+----------+-------+
only showing top 5 rows


Filter

In [0]:
# using show()
purchase_df = oct_events.filter(oct_events.event_type == "purchase")
purchase_df.show(5)

+-------------------+----------+----------+-------------------+--------------------+-------+------+---------+--------------------+
|         event_time|event_type|product_id|        category_id|       category_code|  brand| price|  user_id|        user_session|
+-------------------+----------+----------+-------------------+--------------------+-------+------+---------+--------------------+
|2019-10-01 00:02:14|  purchase|   1004856|2053013555631882655|electronics.smart...|samsung|130.76|543272936|8187d148-3c41-46d...|
|2019-10-01 00:04:37|  purchase|   1002532|2053013555631882655|electronics.smart...|  apple|642.69|551377651|3c80f0d6-e9ec-418...|
|2019-10-01 00:06:02|  purchase|   5100816|2053013553375346967|                NULL| xiaomi| 29.51|514591159|0e5dfc4b-2a55-43e...|
|2019-10-01 00:07:07|  purchase|  13800054|2053013557418656265|furniture.bathroo...|santeri| 54.42|555332717|1dea3ee2-2ded-42e...|
|2019-10-01 00:09:26|  purchase|   4804055|2053013554658804075|electronics.audio...

In [0]:
# using display()
purchase_df = oct_events.filter(oct_events.event_type == "purchase")
purchase_df.display(5)

event_time event_type product_id category_id category_code brand price user_id user_session 2019-10-01T00:02:14.000Z purchase 1004856 2053013555631882655 electronics.smartphone samsung 130.76 543272936 8187d148-3c41-46d4-b0c0-9c08cd9dc564 2019-10-01T00:04:37.000Z purchase 1002532 2053013555631882655 electronics.smartphone apple 642.69 551377651 3c80f0d6-e9ec-4181-8c5c-837a30be2d68 2019-10-01T00:06:02.000Z purchase 5100816 2053013553375346967 null xiaomi 29.51 514591159 0e5dfc4b-2a55-43e6-8c05-97e1f07fbb56 2019-10-01T00:07:07.000Z purchase 13800054 2053013557418656265 furniture.bathroom.toilet santeri 54.42 555332717 1dea3ee2-2ded-42e8-8e7a-4e2ad6ae942f 2019-10-01T00:09:26.000Z purchase 4804055 2053013554658804075 electronics.audio.headphone apple 189.91 524601178 2af9b570-0942-4dcd-8f25-4d84fba82553 2019-10-01T00:09:54.000Z purchase 4804056 2053013554658804075 electronics.audio.headphone apple 161.98 551377651 3c80f0d6-e9ec-4181-8c5c-837a30be2d68 2019-10-01T00:10:08.000Z purchase 1002524 2053013555631882655 electronics.smartphone apple 515.67 524325294 0b74a829-f9d7-4654-b5b0-35bc9822c238 2019-10-01T00:10:56.000Z purchase 6200687 2053013552293216471 appliances.environment.air_heater oasis 28.03 548691404 b67cdbcb-b073-4271-b365-803c6fce53b0 2019-10-01T00:12:14.000Z purchase 4802036 2053013554658804075 electronics.audio.headphone apple 171.56 533624186 e5ac3caa-e6d5-4d6b-ae06-2c18cd9ca683 2019-10-01T00:14:14.000Z purchase 1004932 2053013555631882655 electronics.smartphone vivo 463.31 555083442 83d12d1a-5452-4fa0-abbb-d9f492f8b562 2019-10-01T02:19:10.000Z purchase 1004246 2053013555631882655 electronics.smartphone apple 736.18 515246296 b7dbae4f-cad3-463e-89ce-41990cf48dea 2019-10-01T02:19:12.000Z purchase 13103842 2053013553526341921 null pdw 391.26 516178643 4d74b49e-3838-43cc-ac2e-a0490942b464 2019-10-01T02:19:34.000Z purchase 1005104 2053013555631882655 electronics.smartphone apple 975.57 555160488 a1395546-c124-456c-9752-0f5cf883c63d 2019-10-01T02:19:59.000Z purchase 28100119 2053013564918072245 null null 153.16 517953667 7954f58c-158d-402d-9820-c502a5eea86d 2019-10-01T02:20:11.000Z purchase 4804055 2053013554658804075 electronics.audio.headphone apple 189.91 517129864 df8afa49-66e0-4e54-b9ca-4be6de5c9a0f 2019-10-01T02:20:16.000Z purchase 4700419 2053013560899928785 auto.accessories.videoregister sho-me 141.86 512550575 84f21dc3-df18-4cf3-accd-bcd9655891ca 2019-10-01T02:20:20.000Z purchase 4804295 2053013554658804075 electronics.audio.headphone xiaomi 23.13 540557704 0c990471-9407-4292-a6df-0cbc2f722a40 2019-10-01T02:20:28.000Z purchase 26601440 2053013563517174627 null null 91.12 554101070 5a29c401-c05b-4dcf-b9e6-78324875dfd4 2019-10-01T02:20:33.000Z purchase 1003316 2053013555631882655 electronics.smartphone apple 946.97 516198933 e1050ba4-5425-4b8e-9cc8-194878031718 2019-10-01T02:21:02.000Z purchase 1004659 2053013555631882655 electronics.smartphone samsung 787.18 555168263 d068d08f-aaf3-4949-b031-cdaf49a5c7cf 2019-10-01T02:21:07.000Z purchase 16500007 2053013556462354899 null omron 62.52 516815266 918c33db-9bb0-41b9-a148-47523330eddd 2019-10-01T02:21:45.000Z purchase 28100000 2053013564918072245 null null 60.49 517953667 7954f58c-158d-402d-9820-c502a5eea86d 2019-10-01T02:21:53.000Z purchase 15900073 2053013558190408249 null tefal 38.59 513070042 159b4a84-1687-48a9-a718-10eb8c612bc8 2019-10-01T02:21:59.000Z purchase 4804501 2053013554658804075 electronics.audio.headphone ritmix 3.37 514127317 b332ec72-5344-49e5-a3d5-27507b726259 2019-10-01T02:22:11.000Z purchase 1004750 2053013555631882655 electronics.smartphone samsung 197.43 555110488 ce885079-4d92-4fe6-92a3-377c5a2d8291 2019-10-01T02:22:23.000Z purchase 1307135 2053013558920217191 computers.notebook hp 320.35 514805015 104dc3e4-d6ff-4f00-9031-c0468e75ed4c 2019-10-01T02:22:29.000Z purchase 1500021 2053013552955916539 computers.peripherals.printer epson 116.73 513489079 63de1120-9d48-45d0-b024-500d1b95d71f 2019-10-01T02:22:30.000Z purchase 12703015 2053013553559896355 n

GroupBy

In [0]:
from pyspark.sql.functions import sum

revenue_df = (
    purchase_df
    .groupBy("product_id")
    .agg(sum("price").alias("total_revenue"))
)

revenue_df.show(5)


+----------+-----------------+
|product_id|    total_revenue|
+----------+-----------------+
|   8500290|          4071.73|
|   1005159|        238752.03|
|  27300009|851.1499999999999|
|   5701087|4118.400000000001|
|  18001092|             4.63|
+----------+-----------------+
only showing top 5 rows


OrderBy

In [0]:
top_products = revenue_df.orderBy("total_revenue", ascending=False)

top_products.show(10)


+----------+--------------------+
|product_id|       total_revenue|
+----------+--------------------+
|   1005115|1.2406807350000003E7|
|   1005105|1.0239248679999996E7|
|   1004249|   6730112.920000011|
|   1005135|   5567806.640000007|
|   1004767|   5430723.430000007|
|   1002544|   4855702.389999994|
|   1004856|    3798956.42000002|
|   1002524|   3538299.120000006|
|   1003317|  3051294.2600000016|
|   1004870|   3027098.049999997|
+----------+--------------------+
only showing top 10 rows


Top categories by revenue


In [0]:
category_revenue = (
    purchase_df
    .groupBy("category_id")
    .agg(sum("price").alias("category_revenue"))
    .orderBy("category_revenue", ascending=False)
)

category_revenue.display(10)


category_id category_revenue 2053013555631882655 1.5704962336999926E8 2053013558920217191 8977896.909999993 2053013554415534427 8410385.400000008 2053013563810775923 4658646.590000003 2053013553341792533 4181418.3200000003 2053013554658804075 3539126.9899999737 2053013563911439225 2957648.530000001 2053013553559896355 2925240.2700000037 2053013563584283495 2201397.190000002 2053013563651392361 2153864.7700000014 2053013565983425517 1685623.850000001 2053013561218695907 1472914.4699999997 2172371436436455782 1398082.2999999989 2053013557024391671 1319825.35 2053013552259662037 1142335.7700000003 2053013563970159485 1136315.6699999995 2053013563693335403 1122060.8599999992 2053013561092866779 950705.3399999997 2053013563835941749 870413.1200000006 2053013560555995845 815780.6099999999 2053013556168753601 734039.4400000002 2053013561579406073 636379.1300000001 2053013559792632471 569874.4400000002 2053013553526341921 537726.5399999999 2053013553970938175 523241.79999999993 2053013553853497655 492311.98000000004 2053013557133443581 410478.62 2053013566100866035 404356.03 2053013560346280633 370673.42 2144356630513320518 338361.24999999994 2053013560807654091 335979.3200000001 2053013563173241677 325132.1199999999 2053013553945772349 300022.07999999996 2053013564003713919 299130.6099999999 2053013552326770905 290985.5400000001 2053013554776244595 289689.0599999996 2053013552955916539 288671.1599999999 2053013560899928785 272614.33999999997 2053013563550729061 261919.44999999998 2053013557192163841 260248.90000000005 2053013553375346967 257862.50000000026 2053013563944993659 255830.38999999998 2053013554524586339 254808.37000000008 2053013564641248165 253998.31000000006 2053013554247762257 243589.30000000002 2059484601444729123 229793.05999999994 2053013553031414015 228858.29 2053013566176363511 223777.06 2053013559733912211 215116.37 2053013553056579841 205208.92000000004 2053013563877884791 205012.05000000005 2053013553484398879 204381.85 2053013555816432043 202134.18 2053013552351936731 201925.99000000002 2053013555321504139 191098.24999999994 2053013561185141473 190729.64999999997 2116907525176557699 185720.70999999996 2053013557544485393 178789.97999999998 2053013557166998015 174807.52 2053013555262783879 173638.45000000004 2127425436764865054 173555.75 2053013556311359947 161530.50999999992 2053013560144954031 160726.64 2053013561059312345 159369.15 2053013555355058573 154381.28999999995 2053013556202308035 150600.68000000002 2053013560530830019 140711.99 2053013555095011711 137116.37000000005 2053013555287949705 136998.34999999998 2053013565069067197 133296.26 2053013563424899933 132253.9 2053013565639492569 131628.41 2053013560287560373 129258.88000000002 2053013564918072245 126222.43000000002 2053013554751078769 121868.95999999999 2053013566142809077 117960.65999999997 2053013555464110485 113560.49999999999 2053013552293216471 110755.87 2053013555573162395 110108.22000000006 2053013559868129947 108690.84999999999 2053013554625249641 107321.89000000006 2053013552385491165 107083.16999999998 2053013560497275585 105748.62999999998 2053013563743667055 101509.43999999999 2053013556227473861 100278.39000000001 2053013557670314521 96486.29000000001 2053013554834964853 94174.21000000005 2053013565782098913 92922.24999999999 2053013561277416167 89251.69999999998 2053013557452210699 86030.30999999998 2053013553912217915 84039.46 2053013565228450757 83928.36000000002 2053013555069845885 80290.49000000003 2053013560178508465 78829.5 2053013558249128509 77437.04 2053013556462354899 76823.15000000007 2053013566067311601 76796.08 2053013566310581247 75967.79999999999 2053013554591695207 75062.41000000002 2053013557603205653 71795.91999999998 2134905044833666047 71193.23999999998 2053013556252639687 69058.29999999999 2053013554222596431 66661.49 2053013556487520725 66120.66000000002 2055156924273394455 61746.05 2062461754293617058 61554.670000000006 2053013564674802599 60535.149999999994 2102307650380235197 58010.21000000001 20530135603127

Export as CSV


In [0]:
top_products.write \
    .mode("overwrite") \
    .option("header", True) \
    .csv("/Volumes/workspace/eccomerce/ecommerce_data/top_products_revenue")